In [98]:
import geopandas as gpd
import pandas as pd
import math
import ee
import geemap

In [99]:
ee.Authenticate()
ee.Initialize(project='ee-curuai')

In [100]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


# Import image collections

Landsat 7 - PY6S

In [101]:
landsat7 = ee.ImageCollection("projects/ee-curuai/assets/Py6S/LD7/ld7_py6s")\
            .select([ 'B1', 'B2', 'B3', 'B4', 'B5', 'B7'])
print(ee.Date(landsat7.first().get('system:time_start')).format().getInfo())
print(ee.Date(landsat7.sort('system:time_start',False).first().get('system:time_start')).format().getInfo())

2013-05-12T13:44:05
2017-09-28T13:50:48


Landsat 8 PY6S

In [102]:
landsat8 = (ee.ImageCollection("projects/ee-curuai/assets/Py6S/LD8/ld8_py6s")
            .select(['B2', 'B3', 'B4', 'B5', 'B6', 'B7']))
print(ee.Date(landsat8.first().get('system:time_start')).format().getInfo())
print(ee.Date(landsat8.sort('system:time_start',False).first().get('system:time_start')).format().getInfo())

2013-05-20T13:50:14
2017-09-27T13:54:12


# Transform into remote sensing reflectance and sunglint correction

In [103]:
def deglint (img):
  '''#dividir imagem corrigida por pi
  Rrs_sat_ac = Rsat_ac / pi
  fazer deglint
  Rrs_sat_ac_deglint(VNIR) = Rrs_sat_ac (VNIR) − Rrs_sat_ac (SWIR)
  correção no artigo INPE CURUAI'''
  Rrs = img.divide(math.pi)
  deglint = Rrs.select(['blue_mean','green_mean','red_mean','nir_mean','swir1','swir2'])\
    .subtract(Rrs.select('swir1'))

  return (deglint.updateMask(deglint.select(['red_mean']).gt(0)).updateMask(deglint.select(['blue_mean']).gt(0)).updateMask(deglint.select(['green_mean']).gt(0)).updateMask(deglint.select(['nir_mean']).gt(0))
          .copyProperties(img,['system:time_start','CLOUD_COVER',"system:index"]))

## Padronize band names

In [104]:
name_bands = ['blue_mean','green_mean','red_mean','nir_mean','swir1','swir2']

Landsat 7

In [105]:
#renomear bandas

ld7 = landsat7.map(lambda img: img.rename(name_bands)).map(deglint)
ld7.first()

Landsat 8

In [106]:
ld8 = landsat8.map(lambda img: img.rename(name_bands)).map(deglint)
ld8

# Mask land

In [107]:
# // Function to select water pixels
def hsvComposite (image):
  composite = image.select(['blue_mean','green_mean','red_mean']).rgbToHsv()#.clip(limits);
  hue = composite.select("hue");
  max_mask = hue.lte(0.9)
  min_mask = hue.gte(0.3)
  return image.updateMask(max_mask).updateMask(min_mask);

In [108]:
ld8_masked = ld8.map(hsvComposite)
ld7_masked = ld7.map(hsvComposite)
ld8_masked

# Import Model and Classify Images

In [109]:
classifier = ee.Classifier.load('projects/ee-curuai/assets/RF_regressor')
classifier

In [111]:
predictors = ['blue_mean', 'green_mean','red_mean', 'nir_mean']
ld7_classified = ld7_masked.select(predictors).map(lambda img: img.classify(classifier=classifier).copyProperties(img,['system:index','system:time_start']))
ld7_classified

In [112]:
ld8_classified = ld8_masked.select(predictors).map(lambda img: img.classify(classifier=classifier).copyProperties(img,['system:index','system:time_start']))
ld8_classified

# Import Regression Points

In [151]:
reg_points = geemap.geojson_to_ee('/content/drive/MyDrive/CURUAI_PROCESS/regression_p.geojson')
reg_points_unique = reg_points.distinct('.geo')
reg_points_unique

# Sample images from regression points

In [146]:
merge_classification = ld7_classified.merge(ld8_classified).sort('system:time_start')
merge_classification

In [153]:
projection = ld8.first().select('red_mean').projection()
ld7_classified.map(lambda img: img.sampleRegions(collection = reg_points_unique, properties = ['LONGITUDE''LATITUDE'], scale=30, projection=projection,geometries=True)).first()

In [91]:
Map = geemap.Map(basemap='HYBRID')
roi_points = ee.FeatureCollection('projects/ee-curuai/assets/curuai_points')
Map.centerObject(roi_points,10)
imgld7 = ee.Filter.eq('system:index','BOA_LE07_228061_20130604')
imgld8 = ee.Filter.eq('system:index','BOA_LC08_228061_20140615')

Map.addLayer(ld7.filter(imgld7).first(), {'bands':['red_mean','green_mean','blue_mean'], 'min':0,'max':0.02}, 'ld7')
Map.addLayer(ld8.filter(imgld8).first(), {'bands':['red_mean','green_mean','blue_mean'], 'min':0,'max':0.02}, 'ld8')

Map.addLayer(ld7_masked.filter(imgld7).first(), {'bands':['red_mean','green_mean','blue_mean'], 'min':0,'max':0.02}, 'ld7 masked')
Map.addLayer(ld8_masked.filter(imgld8).first(), {'bands':['red_mean','green_mean','blue_mean'], 'min':0,'max':0.02}, 'ld8 masked')


Map.addLayer(ld7_classified.filter(imgld7).first(), {'palette':['#ffffb2','#fecc5c','#fd8d3c','#e31a1c'], 'min':0,'max':150}, 'classification LD7')
Map.addLayer(ld8_classified.filter(imgld8).first(), {'palette':['#ffffb2','#fecc5c','#fd8d3c','#e31a1c'], 'min':0,'max':150}, 'classification LD8')


Map.addLayer(roi_points, {'color':'darkred'}, 'Data polygon');
Map

Map(center=[-2.184599717160098, -55.49304633852027], controls=(WidgetControl(options=['position', 'transparent…